In [64]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
pd.set_option('mode.chained_assignment', None)

df = pd.read_csv('SPY.csv')
df.columns


Index(['Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume'], dtype='object')

In [65]:
df['Date'] = pd.to_datetime(df['Date'])
df['day_name'] = df['Date'].dt.day_name()
df['date_num'] = df['Date'].dt.day
df['local_min'] = df['Open'].rolling(window=30,min_periods=15).min()

In [66]:
total_cash = 100000
lump_sum = total_cash
num_mondays = df['day_name'][df['day_name'] == 'Monday'].count()
dca_val = total_cash/num_mondays

In [67]:
df['lump_shares'] = pd.Series(dtype='float64')
df['lump_shares'].iloc[0] = lump_sum / df['Open'].iloc[0]
df['lump_shares'].fillna(0, inplace=True)
df['dca_shares'] = dca_val/df['Open'][df['day_name'] == 'Monday']
df['dip_shares'] = dca_val*5/df['Open'][df['Open'] == df['local_min']]
df['original_open'] = df['Open']

In [68]:
total_lump_shares = df['lump_shares'].sum()
total_dca_shares = df['dca_shares'].sum()
total_dip_shares = df['dip_shares'].sum()

print('Lump Shares: {}'.format(total_lump_shares))
print('DCA Shares: {}'.format(total_dca_shares))
print('Dip Shares: {}'.format(total_dip_shares))

Lump Shares: 2274.3425728500356
DCA Shares: 867.8595852987511
Dip Shares: 1386.1394525297474


In [69]:
# df['log_ret'] = np.log(df['Open']) - np.log(df['Open'].shift(1))

# def shuffle_log_ret(df):
#     log_ret = df['log_ret'].drop([0],axis=0)
    
#     log_ret = log_ret.sample(frac = 1).to_list()
#     log_ret = np.insert(log_ret,0,np.nan)  

#     df['log_ret'] = log_ret

#     return df

# def shuffle_open_price_and_log_ret(df):
#     df = shuffle_log_ret(df)

#     ret = df['original_open'].shift(1) * np.exp(df['log_ret'])
#     ret.iloc[0] = df['original_open'].iloc[0]
#     df['Open'] = ret
#     return df

# def perform_strategy_calculations(df):
#     df['lump_shares'] = pd.Series(dtype='float64')
#     df['lump_shares'].iloc[0] = lump_sum / df['Open'].iloc[0]
#     df['lump_shares'].fillna(0, inplace=True)
#     df['dca_shares'] = dca_val/df['Open'][df['day_name'] == 'Monday']
#     df['dip_shares'] = dca_val*5/df['Open'][df['Open'] == df['local_min']]

#     total_lump_shares = df['lump_shares'].sum()
#     total_dca_shares = df['dca_shares'].sum()
#     total_dip_shares = df['dip_shares'].sum()

#     total_lump_val = total_lump_shares*df['Open'].iloc[-1]
#     total_dca_val = total_dca_shares*df['Open'].iloc[-1]
#     total_dip_val = total_dip_shares*df['Open'].iloc[-1]

#     return total_lump_val, total_dca_val, total_dip_val


In [70]:
def shuffle_open_price_and_log_ret(df):
    df['log_ret'] = np.log(df['original_open']) - np.log(df['original_open'].iloc[0])
    df['log_ret_diff'] = df['log_ret'].diff()
    df['log_ret_diff'][1:] = df['log_ret_diff'].iloc[1:].sample(frac = 1).to_list()
    df['log_ret_diffsum'] = df['log_ret_diff'].cumsum()
    df['log_ret'] = df['log_ret_diffsum']
    df['Open'] = np.exp(df['log_ret_diffsum']) * df['original_open'].iloc[0]
    df['Open'].iloc[0] = df['original_open'].iloc[0]

    return df

def perform_strategy_calculations(df):
    df['lump_shares'] = pd.Series(dtype='float64')
    df['lump_shares'].iloc[0] = lump_sum / df['Open'].iloc[0]
    df['lump_shares'].fillna(0, inplace=True)
    df['local_min'] = df['Open'].rolling(window=30,min_periods=15).min()
    df['dca_shares'] = dca_val/df['Open'][df['day_name'] == 'Monday']
    df['dip_shares'] = dca_val*5/df['Open'][df['Open'] == df['local_min']]

    total_lump_shares = df['lump_shares'].sum()
    total_dca_shares = df['dca_shares'].sum()
    total_dip_shares = df['dip_shares'].sum()

    total_lump_val = total_lump_shares*df['Open'].iloc[-1]
    total_dca_val = total_dca_shares*df['Open'].iloc[-1]
    total_dip_val = total_dip_shares*df['Open'].iloc[-1]

    return total_lump_val, total_dca_val, total_dip_val


In [71]:
traces_range = range(1,20)

fig = go.Figure()

fig.add_trace(go.Scatter(
            name = 'Original',
            x = df.index,
            y = df['Open']
    ))

for i in traces_range:
    df = shuffle_open_price_and_log_ret(df)
    fig.add_trace(go.Scatter(
            name = 'Monte {}'.format(i),
            x = df.index,
            y = df['Open']
    ))

fig.show()


In [72]:
def perform_monte_carlo(df,monte_carlo_number=1000):
    monte_carlo_range = range(0,monte_carlo_number)
    val_list = []
    for i in monte_carlo_range:
        df = shuffle_open_price_and_log_ret(df)
        total_lump_val, total_dca_val, total_dip_val = perform_strategy_calculations(df)
        val_list.append([total_lump_val,total_dca_val,total_dip_val])

    return pd.DataFrame(val_list,columns=['lump','dca','dip'])

monte_carlo_df = perform_monte_carlo(df)

In [73]:
import plotly.express as px
import plotly.graph_objects as go


fig = go.Figure()

fig.add_trace(go.Histogram(x=monte_carlo_df['lump'], name='Lump'))
fig.add_trace(go.Histogram(x=monte_carlo_df['dca'], name='DCA'))
fig.add_trace(go.Histogram(x=monte_carlo_df['dip'], name='Dip'))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.75)

fig.update_layout(
    xaxis_title="Value",
    yaxis_title="Count",
)

fig.update_layout(showlegend=True)
fig.show()

In [74]:
import random
random.seed(1)

def test_random_entry(raw_df):
    num_days = len(raw_df)
    random_entry_point = random.randint(50,num_days)

    df = raw_df.copy(deep=True).iloc[random_entry_point:,:]
    df.reset_index(inplace=True)
    lump_sum = total_cash
    num_mondays = df['day_name'][df['day_name'] == 'Monday'].count()
    dca_val = total_cash/num_mondays

    monte_carlo_df = perform_monte_carlo(df,100)

    lump_median = monte_carlo_df['lump'].median()
    dca_median = monte_carlo_df['dca'].median()
    dip_median = monte_carlo_df['dip'].median()

    return lump_median, dca_median, dip_median


In [75]:
df = pd.read_csv('SPY.csv')

df['Date'] = pd.to_datetime(df['Date'])
df['day_name'] = df['Date'].dt.day_name()
df['date_num'] = df['Date'].dt.day
df['local_min'] = df['Open'].rolling(window=30,min_periods=15).min()
df['original_open'] = df['Open']

num_random_entries = 100
random_entry_range = range(0,num_random_entries)

random_investment_list = []
for i in random_entry_range:
   lump, dca, dip = test_random_entry(df)
   random_investment_list.append([lump,dca,dip])

investment_df = pd.DataFrame(random_investment_list,columns=['lump','dca','dip'])

fig = go.Figure()

fig.add_trace(go.Box(
                    name='Lump', 
                    y=investment_df['lump'],
                    ))

fig.add_trace(go.Box(
                    name='DCA', 
                    y=investment_df['dca'],
                    ))

fig.add_trace(go.Box(
                    name='Dip', 
                    y=investment_df['dip'],
                    ))

fig.show()


In [76]:
df = pd.read_csv('SPY.csv')

total_cash = 100000
lump_sum = total_cash
df['Date'] = pd.to_datetime(df['Date'])
df['day_name'] = df['Date'].dt.day_name()
df['local_min'] = df['Open'].rolling(window=30,min_periods=15).min()
num_mondays = df['day_name'][df['day_name'] == 'Monday'].count()
dca_num_installments = 10
dca_val = total_cash/dca_num_installments

df['lump_shares'] = pd.Series(dtype='float64')
df['lump_shares'].iloc[0] = lump_sum / df['Open'].iloc[0]
df['lump_shares'].fillna(0, inplace=True)
df['dca_shares'] = dca_val/df['Open'][df['day_name'] == 'Monday']
df['dip_shares'] = dca_val/df['Open'][df['Open'] == df['local_min']]
df['original_open'] = df['Open']

In [77]:
total_lump_shares = df['lump_shares'].sum()
total_dca_shares = df['dca_shares'].dropna().head(dca_num_installments).sum()
total_dip_shares = df['dip_shares'].dropna().head(dca_num_installments).sum()

print('Lump Shares: {}'.format(total_lump_shares))
print('DCA Shares: {}'.format(total_dca_shares))
print('Dip Shares: {}'.format(total_dip_shares))

Lump Shares: 2274.3425728500356
DCA Shares: 2243.4567579369605
Dip Shares: 2228.9831704675794


In [111]:
def perform_strategy_calculations(df):
    dca_val = total_cash/dca_num_installments
    df['lump_shares'] = pd.Series(dtype='float64')
    df['lump_shares'].iloc[0] = lump_sum / df['Open'].iloc[0]
    df['lump_shares'].fillna(0, inplace=True)
    df['local_min'] = df['Open'].rolling(window=30,min_periods=15).min()
    df['dca_shares'] = dca_val/df['Open'][df['day_name'] == 'Monday']
    df['dip_shares'] = dca_val/df['Open'][df['Open'] == df['local_min']]

    total_lump_shares = df['lump_shares'].sum()
    total_dca_shares = df['dca_shares'].dropna().head(dca_num_installments).sum()
    total_dip_shares = df['dip_shares'].dropna().head(dca_num_installments).sum()

    total_lump_val = total_lump_shares*df['Open'].iloc[-1]
    total_dca_val = total_dca_shares*df['Open'].iloc[-1]
    total_dip_val = total_dip_shares*df['Open'].iloc[-1]

    return total_lump_val, total_dca_val, total_dip_val

In [79]:
monte_carlo_df = perform_monte_carlo(df)

fig = go.Figure()

fig.add_trace(go.Histogram(x=monte_carlo_df['lump']))
fig.add_trace(go.Histogram(x=monte_carlo_df['dca']))
fig.add_trace(go.Histogram(x=monte_carlo_df['dip']))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.75)

fig.update_layout(
    xaxis_title="Value",
    yaxis_title="Count",
)

fig.update_layout(showlegend=True)
fig.show()

In [116]:
def test_random_subset(raw_df, dca_num_installments):
    num_days = len(raw_df)
    random_entry_point = random.randint(0,num_days//2)
    random_exit_point = random.randint(num_days//2,num_days)

    dca_val = total_cash/dca_num_installments

    df = raw_df.copy(deep=True).iloc[random_entry_point:random_exit_point,:]
    df.reset_index(inplace=True)
    lump_sum = total_cash
    num_mondays = df['day_name'][df['day_name'] == 'Monday'].count()

    monte_carlo_df = perform_monte_carlo(df,100)

    lump_median = monte_carlo_df['lump'].median()
    dca_median = monte_carlo_df['dca'].median()
    dip_median = monte_carlo_df['dip'].median()

    return lump_median, dca_median, dip_median

In [117]:
df = pd.read_csv('SPY.csv')

df['Date'] = pd.to_datetime(df['Date'])
df['day_name'] = df['Date'].dt.day_name()
df['date_num'] = df['Date'].dt.day
df['original_open'] = df['Open']

total_cash = 10000

num_random_entries = 100
random_entry_range = range(0,num_random_entries)
dca_num_installments = 10


random_investment_list = []
for i in random_entry_range:
   lump, dca, dip = test_random_subset(df,dca_num_installments)
   random_investment_list.append([lump,dca,dip])

investment_df = pd.DataFrame(random_investment_list,columns=['lump','dca','dip'])

fig = go.Figure()

fig.add_trace(go.Box(
                    name='Lump', 
                    y=investment_df['lump'],
                    ))

fig.add_trace(go.Box(
                    name='DCA', 
                    y=investment_df['dca'],
                    ))

fig.add_trace(go.Box(
                    name='Dip', 
                    y=investment_df['dip'],
                    ))

fig.show()


In [138]:
def explore_dca_installments(input_data_file, num_dca_start, num_dca_end, num_dca_step):
    df = pd.read_csv(input_data_file)

    df['Date'] = pd.to_datetime(df['Date'])
    df['day_name'] = df['Date'].dt.day_name()
    df['date_num'] = df['Date'].dt.day
    df['local_min'] = df['Open'].rolling(window=30,min_periods=15).min()
    df['log_ret'] = np.log(df['Open']) - np.log(df['Open'].shift(1))
    df['original_open'] = df['Open']

    total_cash = 10000

    num_random_entries = 100
    random_entry_range = range(0,num_random_entries)

    dca_installment_range = range(num_dca_start,num_dca_end,num_dca_step)
    fig = go.Figure()

    investment_df_dict = dict()
    for dca_num_installments in dca_installment_range:
        random_investment_list = []
        for i in random_entry_range:
            lump, dca, dip = test_random_subset(df,dca_num_installments)
            random_investment_list.append([lump,dca,dip])

        investment_df = pd.DataFrame(random_investment_list,columns=['lump','dca','dip'])
        investment_df_dict[dca_num_installments] = investment_df


        fig.add_trace(go.Box(
                            name='Lump {}'.format(dca_num_installments), 
                            y=investment_df['lump'],
                            x=['Lump']*len(investment_df['lump']),
                            legendgroup="Lump"
                            ))

        fig.add_trace(go.Box(
                            name='DCA {}'.format(dca_num_installments), 
                            y=investment_df['dca'],
                            x=['DCA']*len(investment_df['dca']),
                            legendgroup="DCA",
                            ))

        fig.add_trace(go.Box(
                            name='Dip {}'.format(dca_num_installments), 
                            y=investment_df['dip'],
                            x=['Dip']*len(investment_df['dip']),
                            legendgroup="Dip",
                            ))

    fig.update_layout(
        yaxis_title='Final Value',
        boxmode='group'
    )

    fig.show()
    
    dca_num_installments_list = []
    lump_median_list = []
    dca_median_list = []
    dip_median_list = []
    for dca_num_installments in investment_df_dict:
        df = investment_df_dict[dca_num_installments]

        lump_median = df['lump'].median()
        dca_median = df['dca'].median()
        dip_median = df['dip'].median()

        dca_num_installments_list.append(dca_num_installments)
        lump_median_list.append(lump_median)
        dca_median_list.append(dca_median)
        dip_median_list.append(dip_median)
        
    fig = go.Figure()

    fig.add_trace(go.Scatter(
                name = 'Lump',
                x = dca_num_installments_list,
                y = lump_median_list
    ))

    fig.add_trace(go.Scatter(
                name = 'DCA',
                x = dca_num_installments_list,
                y = dca_median_list
    ))

    fig.add_trace(go.Scatter(
                name = 'Dip',
                x = dca_num_installments_list,
                y = dip_median_list
    ))

    fig.show()


# 20 Max Installments

In [118]:
explore_dca_installments('SPY.csv',5,22,2)

# 100 Max Installments

In [120]:
explore_dca_installments('SPY.csv',5,106,10)

# Optimal Max Installments

In [124]:
explore_dca_installments('SPY.csv',2,13,1)

# VIXY Analysis

In [139]:
explore_dca_installments('VIXY.csv', 5, 22, 2)
explore_dca_installments('VIXY.csv', 5, 106, 10)
explore_dca_installments('VIXY.csv', 2, 13, 1)